# Crawling PTA & Berita

In [ ]:
!pip install builtwith

  Preparing metadata (setup.py) ... done
  Created wheel for builtwith: filename=builtwith-1.3.4-py3-none-any.whl size=36077 sha256=b6a543532b9a72bcc885e42ed132ed0b2752c2ea799c79cbd14b4e79b856140e
  Stored in directory: /root/.cache/pip/wheels/7f/2d/b2/606e3df914d4aeeab99c4a4e3e9a61673d2293c2e346db00c8
Successfully built builtwith


## 1. Crawling PTA

In [ ]:
import builtwith

# Analisis teknologi yang digunakan
res = builtwith.parse('https://pta.trunojoyo.ac.id')
print(res)

{'web-servers': ['Nginx'], 'javascript-frameworks': ['jQuery', 'jQuery UI']}


## Page & Link Keluar PTA

In [ ]:
import requests
from bs4 import BeautifulSoup

def crawl_website(url):
    try:
        response = requests.get(url)
        response.raise_for_status()  # Raise an error for bad status codes

        soup = BeautifulSoup(response.content, 'html.parser')

        # Ambil semua judul h1, h2, h3
        headings = soup.find_all(['h1', 'h2', 'h3'])
        for heading in headings:
            print(f"{heading.name}: {heading.get_text()}")

        # Ambil semua link
        links = soup.find_all('a', href=True)
        for link in links:
            print(f"URL: {link['href']} | Teks: {link.get_text()}")

    except requests.exceptions.RequestException as e:
        print(f"Terjadi kesalahan saat mengakses {url}: {e}")

# Gunakan fungsi
crawl_website("https://pta.trunojoyo.ac.id/")

h2: Daftar Karya Ilmiah
URL: index.html | Teks: 
URL: # | Teks: 14677Journal
URL: https://pta.trunojoyo.ac.id/ | Teks: Beranda
URL: https://pta.trunojoyo.ac.id/c_search/ | Teks: Pencarian
URL: https://pta.trunojoyo.ac.id/c_template/ | Teks: Download
URL: https://library.trunojoyo.ac.id/detil.php?id=23 | Teks: Petunjuk Upload
URL: https://pta.trunojoyo.ac.id/c_contact/ | Teks: Kontak
URL: # | Teks: STRATEGI PENGEMBANGAN MAKANAN DAN MINUMAN KHAS PULAU GILIGENTING GUNA MENDUKUNG PARIWISATA BERKELANJUTAN
URL: https://pta.trunojoyo.ac.id/welcome/detail/170361100003 | Teks: Selengkapnya
URL: # | Teks: PERUMUSAN SANKSI PIDANA BAGI MASYARAKAT SEKITAR HUTAN YANG MELAKUKAN PENCURIAN KAYU MILIK NEGARA DALAM UNDANG-UNDANG NOMOR 18 TAHUN 2013
URL: https://pta.trunojoyo.ac.id/welcome/detail/170111100053 | Teks: Selengkapnya
URL: # | Teks: Peran Teor Motivasi Herzberg Sebagai Mediator Self Efficacy, Lingkungan Kerja Dalam Meningkatkan Prestasi Kerja Pegawai ( Kantor Jasa Penilai Publik Guntur Eki And

In [ ]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import time
import sys

def get_text_or_na(soup, selectors):
    """Mencoba beberapa selektor untuk menemukan teks, mengembalikan 'N/A' jika tidak ditemukan."""
    for selector in selectors:
        element = soup.select_one(selector)
        if element:
            text = element.get_text(strip=True)
            if text and text.strip():
                return text.strip()
    return 'N/A'

def get_data_from_span(soup, text_contains):
    """Mencari span yang berisi teks tertentu dan mengekstrak nama setelah titik dua."""
    span = soup.select_one(f'span:-soup-contains("{text_contains}")')
    if span:
        text = span.get_text(strip=True)
        if ':' in text:
            return text.split(':', 1)[1].strip()
    return 'N/A'

def get_abstract_robust(soup, keywords):
    """
    Mencari tag heading (b) yang teksnya mengandung salah satu dari kata kunci
    dan mengekstrak paragraf berikutnya.
    """
    for tag_b in soup.find_all('b'):
        tag_text = tag_b.get_text(strip=True)
        if any(keyword.lower() in tag_text.lower() for keyword in keywords):
            parent_div = tag_b.find_parent('div')
            if parent_div:
                next_div_sibling = parent_div.find_next_sibling('div')
                if next_div_sibling:
                    p_tag = next_div_sibling.find('p', align="justify")
                    if p_tag:
                        abstract_text = p_tag.get_text(strip=True)
                        if abstract_text:
                            return abstract_text
    return 'N/A'

def get_total_pages(soup):
    """
    Mengekstrak total jumlah halaman dari navigasi paginasi.
    """
    try:
        pagination = soup.select_one('ol.pagination')
        if pagination:
            last_page_li = pagination.select('li')[-1]
            last_page_link = last_page_li.select_one('a')
            if last_page_link and 'href' in last_page_link.attrs:
                url_path = last_page_link['href']
                return int(url_path.split('/')[-1])
    except (IndexError, ValueError, KeyError):
        pass
    return 1

def scrape_teknik_all_data():
    """
    Scrapes all data from all study programs within the Faculty of Engineering.
    """
    # Hardcoded list of Engineering study programs and their URLs based on inspection
    prodi_data = [
        {'name': 'Teknik Industri', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/9'},
        {'name': 'Teknik Informatika', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/10'},
        {'name': 'Manajemen Informatika', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/11'},
        {'name': 'Teknik Multimedia Dan Jaringan', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/19'},
        {'name': 'Mekatronika', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/20'},
        {'name': 'Teknik Elektro', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/23'},
        {'name': 'Sistem Informasi', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/31'},
        {'name': 'Teknik Mesin', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/32'},
        {'name': 'Teknik Mekatronika', 'url': 'https://pta.trunojoyo.ac.id/c_search/byprod/33'}
    ]

    all_scraped_data = {
        "penulis": [], "judul": [], "pembimbing_pertama": [], "pembimbing_kedua": [],
        "abstrak_indonesia": [], "abstrak_inggris": [], "prodi": []
    }

    total_data_count = 0

    print("--- MULAI PROSES SCRAPING FAKULTAS TEKNIK ---")

    for prodi in prodi_data:
        print(f"\nScraping data for program: {prodi['name']}")
        print("-" * 50)

        first_page_url = prodi['url']
        try:
            r = requests.get(first_page_url)
            r.raise_for_status()
            soup = BeautifulSoup(r.content, "html.parser")
            total_pages = get_total_pages(soup)
            print(f"Found {total_pages} pages for {prodi['name']}")
        except requests.exceptions.RequestException as e:
            print(f"Error fetching first page for {prodi['name']}: {e}", file=sys.stderr)
            total_pages = 1

        for i in range(1, total_pages + 1):
            url = f"{prodi['url']}/{i}"

            try:
                r = requests.get(url)
                r.raise_for_status()
                soup = BeautifulSoup(r.content, "html.parser")
                jurnals = soup.select('li[data-cat="#luxury"]')

                if not jurnals:
                    print(f"No more journals found on page {i}. Stopping for this program.")
                    break

                for jurnal in jurnals:
                    jurnal_url = jurnal.select_one('a.gray.button')['href']

                    try:
                        response = requests.get(jurnal_url)
                        response.raise_for_status()
                        soup1 = BeautifulSoup(response.content, "html.parser")
                        isi = soup1.select_one('div#content_journal')

                        if isi:
                            judul = get_text_or_na(isi, ['a.title', 'b.title', 'h2.title'])
                            penulis = get_data_from_span(isi, "Penulis")
                            pembimbing_pertama = get_data_from_span(isi, "Dosen Pembimbing I")
                            pembimbing_kedua = get_data_from_span(isi, "Dosen Pembimbing II")
                            abstrak_indonesia = get_abstract_robust(isi, ["Abstraksi", "Abstrak"])
                            abstrak_inggris = get_abstract_robust(isi, ["Abstraction", "Abstract", "ABSTRACT"])

                            all_scraped_data["penulis"].append(penulis)
                            all_scraped_data["judul"].append(judul)
                            all_scraped_data["pembimbing_pertama"].append(pembimbing_pertama)
                            all_scraped_data["pembimbing_kedua"].append(pembimbing_kedua)
                            all_scraped_data["abstrak_indonesia"].append(abstrak_indonesia)
                            all_scraped_data["abstrak_inggris"].append(abstrak_inggris)
                            all_scraped_data["prodi"].append(prodi['name'])

                            total_data_count += 1

                            # Print all data for the current entry
                            print(f"\n--- Data #{total_data_count} ---")
                            print(f"Prodi: {prodi['name']}")
                            print(f"Penulis: {penulis}")
                            print(f"Judul: {judul}")
                            print(f"Pembimbing 1: {pembimbing_pertama}")
                            print(f"Pembimbing 2: {pembimbing_kedua}")
                            print(f"Abstrak Indonesia: {abstrak_indonesia}")
                            print(f"Abstrak Inggris: {abstrak_inggris}")

                    except Exception as e:
                        print(f"ERROR: An error occurred while processing URL: {jurnal_url} - {e}", file=sys.stderr)

                time.sleep(1)

            except requests.exceptions.RequestException as e:
                print(f"Error fetching URL {url}: {e}", file=sys.stderr)
                continue

    df = pd.DataFrame(all_scraped_data)
    df.to_csv("pta_teknik_complete.csv", index=False)
    print("\n---")
    print(f"Scraping finished. Total data scraped: {total_data_count}")
    print("Data saved to pta_teknik_complete.csv")
    print("---")
    return df

# Run the full scraping process
scrape_teknik_all_data()

--- MULAI PROSES SCRAPING FAKULTAS TEKNIK ---

Scraping data for program: Teknik Industri
--------------------------------------------------
Found 143 pages for Teknik Industri

--- Data #1 ---
Prodi: Teknik Industri
Penulis: Siliwangi Fitra Rachmawanto S.T.
Judul: OPTIMASI PEMILIHAN PORTOFOLIO SAHAM PERUSAHAAN SEKTOR TAMBANG DENGAN MENGGUNAKAN GOAL PROGRAMMING
Pembimbing 1: Heri Awalul Ilhamsah S.T., M.T.
Pembimbing 2: Retno Indriartiningtias S.T., M.T.
Abstrak Indonesia: Portofolio adalah sekumpulan saham yang dimiliki investor. Dalam setiap saham pada portofolio memiliki resiko yang harus diminimalkan dengan cara diversifikasi yaitu dengan mengalokasikan dana pada berbagai alternatif investasi pada kombinasi saham pada portofolio. Pada skripsi ini, saham yang digunakan berupa saham dari perusahan sektor tambang yang terdapat 4 subsektor didalamnya yaitu subsektor Batubara, subsektor batu-batuan, subsektor logam dan mineral lainnya, dan subsektor minyak dan gas bumi. Dari setiap subs

ERROR: An error occurred while processing URL: https://pta.trunojoyo.ac.id/welcome/detail/120451100053 - HTTPSConnectionPool(host='pta.trunojoyo.ac.id', port=443): Max retries exceeded with url: /welcome/detail/120451100053 (Caused by SSLError(SSLEOFError(8, '[SSL: UNEXPECTED_EOF_WHILE_READING] EOF occurred in violation of protocol (_ssl.c:1032)')))



--- Data #1757 ---
Prodi: Manajemen Informatika
Penulis: Muhammad Abdullah Firdaus
Judul: SISTEM INFORMASI GEOGRAFIS LUAS PANEN, PRODUKSI DAN PRODUKTIFITAS 
TANAMAN PANGAN KABUPATEN BANGKALAN
Pembimbing 1: Budi Dwi Satoto S.T, M.Kom
Pembimbing 2: -
Abstrak Indonesia: Bangkalan  merupakan  Kabupaten  yang  cukup  agraris  dari  segi  pertanian.  Hal  itu  terbukti  dengan  masih 
banyaknya  lahan  pertanian  di  Bangkalan.  Untuk  mengetahui  seberapa  besarpenggunaanlahan  pertanian 
dibutuhkan suatu sistem informasi yang mendukung akan hal tersebut. Salah satu teknologi yang memfasilitasi 
hal tersebut adalah dengan menggunakan sistem informasi geografis(SIG).
Penelitian  ini  bertujuan  untuk  mengatasi masalah  yang  berhubungan  dengan  pemetaan  daerah  penanaman 
tanaman  pangan  di  Bangkalan  dengan  memanfaatkan  komputer  sebagai  media  pemberi  informasi  dan 
menampilkan  informasi  kepada  masyarakat  mengenai  komoditi  hasil  pertaniaan  pada  khususnya  tanaman 
panga

penulis  \
0     Siliwangi Fitra Rachmawanto S.T.   
1                         AHMAD MAS'UD   
2                    Yulianto Fauzanta   
3                    M Mundir Muhlisin   
4                             Muhibbin   
...                                ...   
2288                   Raudatul Jannah   
2289                        Ach. Dafid   
2290                         MOH HOLIL   
2291                 Ach Imam Sudianto   
2292                MOH TAUFIK HIDAYAT   

                                                  judul  \
0     OPTIMASI PEMILIHAN PORTOFOLIO SAHAM PERUSAHAAN...   
1     PERANCANGAN TATA LETAK FASILITAS LANTAI PRODUK...   
2     PERUMUSAN STRATEGI BISNIS UD. BUDI JAYA BANGKA...   
3     USULAN PERBAIKAN UTILITAS RESOURCES PADA LANTA...   
4     Peningkatan Kepuasan Masyarakat Terhadap Pelay...   
...                                                 ...   
2288  ROBOT PENDETEKSI LOKASI KEBOCORAN PADA PIPA LI...   
2289  SISTEM KENDALI KADAR Ph DAN TEMPERATUR TAMBAK ...   
2290  PERANCANGAN PROTOTIPE ALAT PENUKAR \nPANAS MEN...   
2291  PEMANFAATAN ANTI-ROLL TERHADAP KESEIMBANGAN KAPAL   
2292  ALAT PENGGULUNG UNTUK MENGATUR KERAPATAN KERTA...   

                      pembimbing_pertama                     pembimbing_kedua  \
0        Heri Awalul Ilhamsah S.T., M.T.   Retno Indriartiningtias S.T., M.T.   
1           SABARUDIN AKHMAD, S.T., M.T.           SUGENG PURWOKO, S.T., M.T.   
2              Fitri Agustina, S.T., M.T   Retno Indriartiningtias, S.T., M.T   
3                          Mu'alim ST MT                 Sugeng Purwoko ST MT   
4                         Rahmad Hidayat              Retno Indriartiningtias   
...                                  ...                                  ...   
2288             Vivi Tri .W, S.Kom.,MT.              Hairil Budiarto,ST.,MT.   
2289  Vivi Tri Widyaningrum, S.Kom.,M.T.            Hairil Budiarto,S.T.,M.T.   
2290      AHMAD SAHRU ROMADHON.,S.Kom.MT               HAIRIL BUDIARTO.,ST.MT   
2291           Hairil Budiarto S.T., M.T  Vivi Tri Widyanningrum S.Kom., M.T.   
2292           FAIKUL UMAM., S.KOM., M.T            SRI WAHYUNI., S.KOM., M.T   

                                      abstrak_indonesia  \
0     Portofolio adalah sekumpulan saham yang dimili...   
1     PT. ABC merupakan perusahaan yang bergerak dib...   
2     Bangkalan merupakan salah satu kabupaten yang ...   
3     Simulasi adalah duplikasi atau abstraksi dari ...   
4     Kepuasan adalah tingkat perasaan seseorang ter...   
...                                                 ...   
2288  LPG adalah singkatan dari Liquefied Petroleum ...   
2289  Komoditas hewan air yang mampu mengahasilkan d...   
2290  Perancangan Prototype alat ini dilakukan karen...   
2291  Kapal adalah alat transportasi pengangkut penu...   
2292  ABSTRAK\n\nKertas merupakan kebutuhan yang dib...   

                                        abstrak_inggris               prodi  
0     Portofolio is a collection of stock owned by i...     Teknik Industri  
1     PT. ABC is a company engaged in the manufactur...     Teknik Industri  
2     Bangkalan is one of the districts that have th...     Teknik Industri  
3     Simulation is a duplication or abstraction of ...     Teknik Industri  
4     Satisfaction is feeling level of someone to se...     Teknik Industri  
...                                                 ...                 ...  
2288  LPG stands for Liquefied Petroleum Gas which m...  Teknik Mekatronika  
2289  Animal water commodities capable of producing ...  Teknik Mekatronika  
2290  Prototype design tool is done because the medi...  Teknik Mekatronika  
2291  The ship is a means of transporting passengers...  Teknik Mekatronika  
2292  ABSTRACT\n\nPaper is a necessity needed by hum...  Teknik Mekatronika  

[2293 rows x 7 columns]

In [ ]:
import os
import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin, urlparse

# Konfigurasi
URL = "https://mulaab.github.io"  # Website target
FOLDER_NAME = "gambar"             # Folder untuk simpan gambar
HEADERS = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36'
}

# Buat folder jika belum ada
if not os.path.exists(FOLDER_NAME):
    os.makedirs(FOLDER_NAME)
    print(f"Folder '{FOLDER_NAME}' berhasil dibuat.")

# Ambil halaman web
try:
    response = requests.get(URL, headers=HEADERS, timeout=10)
    response.raise_for_status()
except requests.exceptions.RequestException as e:
    print(f"Gagal mengakses {URL}: {e}")
    exit()

# Parse HTML dengan BeautifulSoup
soup = BeautifulSoup(response.content, 'html.parser')

# Cari semua tag <img>
images = soup.find_all('img')
print(f"Ditemukan {len(images)} gambar di halaman {URL}.")

# List untuk menyimpan URL gambar
image_urls = []

for i, img in enumerate(images):
    # Ambil atribut src
    src = img.get('src')
    if not src:
        print(f"Gambar ke-{i+1} tidak memiliki atribut 'src', dilewati.")
        continue

    # Konversi URL relatif ke absolut
    img_url = urljoin(URL, src)
    image_urls.append(img_url)

    # Ambil nama file dari URL
    parsed_url = urlparse(img_url)
    filename = os.path.basename(parsed_url.path)

    # Validasi nama file
    if not filename or '.' not in filename:
        ext = '.jpg'
        filename = f"image_{i+1}{ext}"

    # Pastikan ekstensi file valid
    valid_exts = ('.png', '.jpg', '.jpeg', '.gif', '.webp', '.svg')
    if not filename.lower().endswith(valid_exts):
        filename += '.jpg'

    # Path lokal
    file_path = os.path.join(FOLDER_NAME, filename)

    # Download gambar
    try:
        img_response = requests.get(img_url, headers=HEADERS, timeout=10)
        img_response.raise_for_status()

        with open(file_path, 'wb') as f:
            f.write(img_response.content)

        print(f"Berhasil download: {filename} -> {file_path}")

    except Exception as e:
        print(f"Gagal download {img_url}: {e}")

# Ringkasan
print("\nCrawling selesai!")
print(f"Semua gambar disimpan di: ./{FOLDER_NAME}")
print(f"Total gambar diproses: {len(image_urls)}")

Folder 'gambar' berhasil dibuat.
Ditemukan 3 gambar di halaman https://mulaab.github.io.
Berhasil download: avatar_hubbf8cd69e817f868f48e6cd8dbaf10a0_30117_250x250_fill_q90_lanczos_center.jpg -> gambar\avatar_hubbf8cd69e817f868f48e6cd8dbaf10a0_30117_250x250_fill_q90_lanczos_center.jpg
Berhasil download: featured_huad4ca000f548177c81ea8fc52ac135a6_195982_150x0_resize_q90_lanczos.jpg -> gambar\featured_huad4ca000f548177c81ea8fc52ac135a6_195982_150x0_resize_q90_lanczos.jpg
Berhasil download: featured_hu3888f6a4f517b25077a8f129d425e8d6_206332_150x0_resize_lanczos_2.png -> gambar\featured_hu3888f6a4f517b25077a8f129d425e8d6_206332_150x0_resize_lanczos_2.png

Crawling selesai!
Semua gambar disimpan di: ./gambar
Total gambar diproses: 3


## Crawling Berita

In [1]:
import requests
from bs4 import BeautifulSoup
import time
import re
import string
import sys
import pandas as pd
from requests.adapters import HTTPAdapter
from urllib3.util.retry import Retry
import random

# === Fungsi Tampilan Progress Bar ===
def print_progress_bar(prefix, current, total, length=30):
    """Tampilkan progress bar untuk memantau proses scraping."""
    percent = (current / total) * 100 if total > 0 else 0
    filled = int(length * current // total)
    bar = '█' * filled + '-' * (length - filled)
    sys.stdout.write(f'\r{prefix} |{bar}| {percent:.1f}% ({current}/{total})')
    sys.stdout.flush()
    if current == total:
        sys.stdout.write('\n')

# === Konfigurasi Session dengan Retry ===
def get_session():
    session = requests.Session()
    retry_strategy = Retry(
        total=5,
        status_forcelist=[429, 500, 502, 503, 504],
        allowed_methods=["GET"],
        backoff_factor=1
    )
    adapter = HTTPAdapter(max_retries=retry_strategy)
    session.mount("https://", adapter)
    return session

# === Ambil Judul & Konten Artikel ===
def get_article_content_and_title(session, url):
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/108.0.0.0 Safari/537.36'
    }
    try:
        r = session.get(url, headers=headers, timeout=15)
        r.raise_for_status()
        soup = BeautifulSoup(r.text, "html.parser")

        title = get_article_title(soup)
        content_selectors = [
            "div.detail-konten", "div.news-detail__content", "div.itp_bodycontent",
            "div.content-text", "div.article-content", "div.text_area"
        ]

        paragraphs = []
        for selector in content_selectors:
            content_divs = soup.select(selector)
            if content_divs:
                for div in content_divs:
                    for p in div.find_all("p"):
                        text = p.get_text(strip=True)
                        if text and not text.lower().startswith("baca juga"):
                            paragraphs.append(text)
                if paragraphs:
                    break
        
        if not paragraphs:
            body_text = soup.find("article")
            if body_text:
                for p in body_text.find_all("p"):
                    text = p.get_text(strip=True)
                    if text and not text.lower().startswith("baca juga"):
                        paragraphs.append(text)

        content = " ".join(paragraphs)
        return title, content
    except requests.exceptions.RequestException as e:
        print(f"Error fetching {url}: {e}", file=sys.stderr)
        return "Judul Tidak Ditemukan", ""

# === Ambil Judul dari Elemen HTML ===
def get_article_title(soup):
    title_tag = soup.find("h1", class_="detail-title")
    if title_tag:
        return title_tag.get_text(strip=True)
    
    title_tag = soup.find("h2", class_="media__title")
    if title_tag:
        return title_tag.get_text(strip=True)
        
    title_tag = soup.find("title")
    if title_tag:
        return title_tag.get_text(strip=True).replace(" - detiknews", "").replace(" - detikfinance", "")

    return "Judul Tidak Ditemukan"

# === Ekstrak ID dari URL ===
def extract_id(url):
    id_match_d = re.search(r"/d-(\d+)", url)
    if id_match_d:
        return id_match_d.group(1)
    id_match_end = re.search(r"-(\d+)$", url)
    if id_match_end:
        return id_match_end.group(1)
    id_match_middle = re.search(r"(\d+)\.html$", url)
    if id_match_middle:
        return id_match_middle.group(1)
    return None

# === Fungsi Utama Scraping ===
def berita(categories, pages_per_category=10, max_per_category=100):
    start_time = time.time()
    session = get_session()
    all_articles_data = []
    processed_links = set()

    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/108.0.0.0 Safari/537.36'
    }

    base_urls = {
        "politik": "https://news.detik.com/indeks/berita/",
        "hukum": "https://news.detik.com/indeks/berita/",
        "ekonomi": "https://finance.detik.com/indeks/",
        "detikx": "https://news.detik.com/x/indeks/",
        "hiburan": "https://hot.detik.com/indeks/",
        "internasional": "https://news.detik.com/indeks/berita/",
        "sepakbola": "https://sport.detik.com/sepakbola/indeks/",
        "olahraga": "https://sport.detik.com/indeks/",
        "lingkungan": "https://www.detik.com/tag/lingkungan",
        "otomotif": "https://oto.detik.com/indeks"
    }

    for cat in categories:
        total_collected = 0
        print(f"\n🌐 Memulai crawling kategori: {cat}")
        
        for page_count in range(1, pages_per_category + 1):
            if total_collected >= max_per_category:
                break

            url = f"{base_urls.get(cat.lower(), f'https://{cat.lower()}.detik.com/indeks/')}"
            if cat.lower() == "lingkungan":
                url = f"https://www.detik.com/tag/lingkungan"
            url = f"{url}?page={page_count}"

            try:
                r = session.get(url, headers=headers, timeout=15)
                r.raise_for_status()
                soup = BeautifulSoup(r.text, "html.parser")
                article_links = soup.select("a.media__link")

                for a in article_links:
                    link = a.get("href")
                    if not link or link in processed_links:
                        continue
                    processed_links.add(link)

                    berita_id = extract_id(link)
                    title, content = get_article_content_and_title(session, link)

                    if content:
                        all_articles_data.append({
                            "id_berita": berita_id,
                            "judul_berita": title,
                            "isi_berita_original": content,
                            "kategori_berita": cat
                        })
                        total_collected += 1
                        print_progress_bar(f"{cat}", total_collected, max_per_category)

                    if total_collected >= max_per_category:
                        break

                    time.sleep(random.uniform(1, 2))

            except requests.exceptions.RequestException as e:
                print(f"\n❌ Gagal mengakses {url}: {e}", file=sys.stderr)
                break

        print(f"\n✅ Selesai kategori {cat} — Total berita: {total_collected}")

    # === Simpan ke CSV ===
    df = pd.DataFrame(all_articles_data)
    df.to_csv("crawling_detik_berita.csv", index=False, encoding="utf-8-sig")

    # === Statistik Waktu ===
    end_time = time.time()
    elapsed = int(end_time - start_time)
    jam, sisa = divmod(elapsed, 3600)
    menit, detik = divmod(sisa, 60)

    print("\n🎉 Semua kategori selesai di-scrape!")
    print(f"📊 Total berita terkumpul: {len(df)}")
    print(f"⏱️ Durasi: {jam} jam {menit} menit {detik} detik")
    print("\nBerikut 5 data pertama:\n", df.head())

    return df

if __name__ == '__main__':
    categories = ["politik", "hukum", "ekonomi", "lingkungan", "hiburan", "internasional", "otomotif", "olahraga", "sepakbola"]
    berita(categories, pages_per_category=10, max_per_category=100)



🌐 Memulai crawling kategori: politik
politik |██████████████████████████████| 100.0% (100/100)

✅ Selesai kategori politik — Total berita: 100

🌐 Memulai crawling kategori: hukum
hukum |█████████████████████████████-| 99.0% (99/100)
✅ Selesai kategori hukum — Total berita: 99

🌐 Memulai crawling kategori: ekonomi
ekonomi |██████████████████████████████| 100.0% (100/100)

✅ Selesai kategori ekonomi — Total berita: 100

🌐 Memulai crawling kategori: lingkungan

✅ Selesai kategori lingkungan — Total berita: 0

🌐 Memulai crawling kategori: hiburan
hiburan |██████████████████████████████| 100.0% (100/100)

✅ Selesai kategori hiburan — Total berita: 100

🌐 Memulai crawling kategori: internasional
internasional |------------------------------| 2.0% (2/100)
✅ Selesai kategori internasional — Total berita: 2

🌐 Memulai crawling kategori: otomotif
otomotif |██████████████████████████████| 100.0% (100/100)

✅ Selesai kategori otomotif — Total berita: 100

🌐 Memulai crawling kategori: olahraga
ola